In [4]:
# https://ipython-books.github.io/116-applying-digital-filters-to-speech-sounds/

import sys
import pydub
import tempfile
import numpy as np
from io import BytesIO
import scipy.signal as sg
import matplotlib.pyplot as plt
from IPython.display import Audio, display

np.set_printoptions(threshold=100)
AUDIO_FILE = "audios/eUn7suerUXc-347d051.mp3"


def read(f, normalized=False):
    """MP3 to numpy array"""
    a = pydub.AudioSegment.from_mp3(f)
    y = np.array(a.get_array_of_samples())
    # if a.channels == 2:
    #     y = y.reshape((-1, 2))
    if normalized:
        return a.frame_rate, np.float32(y) / 2**15
    else:
        return a.frame_rate, y

def write(f, sr, x, normalized=False):
    """numpy array to MP3"""
    channels = 2 if (x.ndim == 2 and x.shape[1] == 2) else 1
    if normalized:  # normalized array - each item should be a float in [-1, 1)
        y = np.int16(x * 2 ** 15)
    else:
        y = np.int16(x)
    song = pydub.AudioSegment(y.tobytes(), frame_rate=sr, sample_width=2, channels=channels)
    song.export(f, format="mp3", bitrate="320k")


def play(data, fr):
    display(Audio(data, rate=fr, autoplay=False))


fr, data = read(AUDIO_FILE, normalized=True)
play(data,fr*2)
print(fr)

44100


In [7]:
fig, ax = plt.subplots(1, 1, figsize=(8, 4))
t = np.linspace(0., len(data) / fr, len(data))
ax.plot(t, data, lw=1)

In [8]:
b, a = sg.butter(4, 150 / (fr / 2), 'low')
data_filt = sg.filtfilt(b, a, data)
play(data_filt, fr*2)

fig, ax = plt.subplots(1, 1, figsize=(12, 6))
t = np.linspace(0., len(data_filt) / fr, len(data_filt))
ax.plot(t, data_filt, lw=1)

In [9]:
data_filt

array([-0.0346032 , -0.03402337, -0.03344499, ...,  0.17870442,
        0.17870426,  0.17870414])

In [11]:
np.max(data_filt)

0.7625594490553427

In [14]:
data_filt.shape[0]/fr

40.08

In [15]:
audio = pydub.AudioSegment.from_mp3(AUDIO_FILE)
with tempfile.TemporaryFile() as fn:
    wavef = audio.export(fn, format='wav')
    wavef.seek(0)
    wave = wavef.read()
# We get the raw data by removing the 24 first
# bytes of the header.
x = np.frombuffer(wave, np.int16)[24:] / 2.**15
x

array([-0.04675293, -0.00405884, -0.06381226, ...,  0.20349121,
        0.09268188,  0.14202881])

In [16]:
x.shape

(1767526,)

In [17]:
data_filt.shape

(1767528,)

In [26]:
from scipy.io import wavfile

file = "test.wav"
audio = pydub.AudioSegment.from_mp3(AUDIO_FILE)
audio = audio.set_channels(1)
audio.export(file, format='wav')

samplerate, data = wavfile.read(file)
data

array([ 1443,  -833, -2099, ...,  5027,  5613,  3845], dtype=int16)

In [27]:
data.shape

(883764,)

In [28]:
np.float32(data)/2**15

array([ 0.04403687, -0.02542114, -0.0640564 , ...,  0.15341187,
        0.17129517,  0.11734009], dtype=float32)